In [1]:
import tensorflow as tf
import cv2
import numpy as np
from tensorflow.python.saved_model import tag_constants
import time
import PIL

/home/hui/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/hui/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/hui/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/hui/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:529: FutureWarnin

In [2]:
image = cv2.imread("./demo/db1.jpg",)
image_raw = cv2.resize(cv2.imread("./demo/db1.jpg"),(224,224))
image = cv2.resize(image, (224,224))
image = np.expand_dims(image, axis=0)

In [3]:
image.shape

(1, 224, 224, 3)

In [3]:
graph2 = tf.Graph()
graph2.as_default()
sess  = tf.Session(graph=graph2)
print('\nRestoring...')
tf.saved_model.loader.load(
    sess,
    [tag_constants.SERVING],
    "./"
)


Restoring...
Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.loader.load or tf.compat.v1.saved_model.load. There will be a new function for importing SavedModels in Tensorflow 2.0.
Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from ./variables/variables


meta_info_def {
  stripped_op_list {
    op {
      name: "Add"
      input_arg {
        name: "x"
        type_attr: "T"
      }
      input_arg {
        name: "y"
        type_attr: "T"
      }
      output_arg {
        name: "z"
        type_attr: "T"
      }
      attr {
        name: "T"
        type: "type"
        allowed_values {
          list {
            type: DT_BFLOAT16
            type: DT_HALF
            type: DT_FLOAT
            type: DT_DOUBLE
            type: DT_UINT8
            type: DT_INT8
            type: DT_INT16
            type: DT_INT32
            type: DT_INT64
            type: DT_COMPLEX64
            type: DT_COMPLEX128
            type: DT_STRING
          }
        }
      }
    }
    op {
      name: "Assign"
      input_arg {
        name: "ref"
        type_attr: "T"
        is_ref: true
      }
      input_arg {
        name: "value"
        type_attr: "T"
      }
      output_arg {
        name: "output_ref"
        type_attr: "T"
        

In [4]:
net_image_in = graph2.get_tensor_by_name('image:0')

In [5]:
net_image_in = graph2.get_tensor_by_name('image:0')

net_scores = graph2.get_tensor_by_name('scores:0')
net_logits = graph2.get_tensor_by_name("logits:0")
net_scores_dense = graph2.get_tensor_by_name("scores_dense:0")
net_local_desc = graph2.get_tensor_by_name('local_descriptors:0')
net_global_decs = graph2.get_tensor_by_name("global_descriptor:0")
net_local_desc_map = graph2.get_tensor_by_name("local_descriptor_map:0")
results = sess.run([net_scores,
          net_scores_dense,
          net_logits,
          net_local_desc,
          net_global_decs,
          net_local_desc_map],
          feed_dict = {net_image_in: image})

In [106]:
st = time.time()
results = sess.run([net_scores,
          net_scores_dense,
          net_logits,
          net_local_desc,
#           net_global_decs,
          net_local_desc_map],
          feed_dict = {net_image_in: image})
ed = time.time()
print(ed-st)

0.03816652297973633


In [73]:
results[0].shape

(1, 224, 224)

In [74]:
keypoints = tf.where(tf.greater_equal(net_scores[0], 0.01))
# scores = tf.gather_nd(net_scores[0], keypoints)
# 

In [75]:
result_keypoints = sess.run(keypoints, 
                            feed_dict={net_scores: results[0]})

In [77]:
[cv2.circle(image_raw, (i[0],i[1]), int(1), (255, 0, 0), 2) for i in result_keypoints[..., ::-1]]

[array([[[255, 253, 254],
         [254, 251, 253],
         [255, 251, 254],
         ...,
         [163, 210, 254],
         [159, 204, 248],
         [158, 203, 243]],
 
        [[253, 249, 254],
         [252, 249, 254],
         [255, 249, 255],
         ...,
         [157, 206, 252],
         [156, 203, 247],
         [160, 206, 246]],
 
        [[255, 248, 255],
         [254, 247, 254],
         [255, 251, 255],
         ...,
         [149, 199, 245],
         [157, 204, 248],
         [156, 202, 243]],
 
        ...,
 
        [[ 65,  63,  63],
         [ 63,  63,  63],
         [ 64,  64,  64],
         ...,
         [149, 152, 150],
         [152, 153, 151],
         [149, 150, 148]],
 
        [[ 64,  62,  62],
         [ 63,  63,  63],
         [ 61,  61,  61],
         ...,
         [152, 155, 153],
         [152, 153, 151],
         [154, 155, 153]],
 
        [[ 67,  65,  65],
         [ 62,  62,  62],
         [ 58,  58,  57],
         ...,
         [151, 153, 153],
  

In [79]:
PIL.Image.fromarray(image_raw)